<a id="top" style="float:left;" href="http://dynfluid.ensam.eu/"><img style="height:80px;" src="https://hpp.education/Lessons/docet.png"/></a>
<a style="float:right;" href="http://www.cnam.fr//"><img style="height:80px;" src="https://upload.wikimedia.org/wikipedia/commons/6/66/Logo_cnam.gif"/></a>

<center>
<h3 style="color:#888888;"> <i>--  AER004: Mécanique des fluides appliquée  --</i> </h3>
<h1> TN n°3 </h1>
<h3> Abaque numérique </h3>
<h6><a href="mailto:simon.marie@lecnam.net">simon.marie@lecnam.net</a></h6>
</center>

Pour ceux qui ne seraient pas familier avec le language python, vous pouvez consulter le Notebook <a href="https://hpp.education/Lessons/Python/Intro_python.html">Introduction au Python</a>.

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import math
import copy

L'abaque de Moody-Moutine est utilisé pour déterminer graphiquement le coefficient de perte de charge linéaire $\lambda$ en fonction du nombre de Reynolds. On peux alors envisager de définir une version numérique sous la forme d'une fonction qui renvoi la valeur de $\lambda$ en fonction du Reynolds et éventuellement de la rugosité relative $r$.

On rappelle les principales formules:

**Laminaire**:
$$
\lambda=\dfrac{64}{Re}
$$

**Blasius**:
$$
\lambda=\dfrac{0.316}{Re^{1/4}}
$$

**Nikuradse**:
$$
\lambda=0.0032+0.221 R_e^{-0.237}
$$

**IdelCik**:
$$
\lambda=\dfrac{1}{(1.8 \log_{10}(R_e)-1.64)^2}
$$


**Karman-Nikuradse**:
$$
\lambda=\dfrac{1}{(2 \log_{10}(R_e \sqrt{\lambda})-0.8)^2}
$$


**Collebrook**:
$$
\dfrac{1}{\sqrt{\lambda}}=-2 \log_{10}\left( \dfrac{2.51}{Re\sqrt{\lambda}}+\dfrac{r}{3.71} \right)
$$

**Nikuradse - Rugueux**:
$$
\lambda=\dfrac{1}{[1.14-2\log_{10}(r)]^2}
$$



On peut donc définir des fonctions associées aux principales formules des pertes de charges en régime turbulent :

In [ ]:
# Blasius (turbulent lisse):
def Blasius(Re):
	l=0.316*Re**(-0.25)
	return l

# Nikuradse simple (turbulent lisse):
def Nikuradse(Re):
	l=0.0032+0.221*Re**(-0.237)
	return l

# IdelCik (turbulent lisse):
def IdelCik(Re):
	l=1./((1.8*math.log10(Re)-1.64)**2)
	return l

# Nikuradse implicite (turbulent lisse)
def K_Nikuradse(Re):
    # On supose une valeur initiale pour l (par exemple Blasius):
	l=Blasius(Re)
    # On calcul la nouvelle valeur de l avec la formule de Nikuradse:
	l2=1./(2*math.log10(Re*math.sqrt(l))-0.8)**2
	i=0;
    # On recommence tant que la difference entre les deux est plus grande que 0.0001
	while abs(l2-l)>1e-4:
		i+=1
		l=copy.copy(l2)
		l2=1./(2*math.log10(Re*math.sqrt(l))-0.8)**2
	return l2

# Collebrook implicite (Turbulent intermédiaire):
def Collebrook(Re,r):
	l=Nikuradse(Re)
	l2=1./(-2.*math.log10((2.51/(Re*math.sqrt(l)))+r*(1./3.71)))**2
	i=0;
	while abs(l2-l)>1e-4:
		i+=1
		l=l2
		l2=1./(-2.*math.log10((2.51/(Re*math.sqrt(l)))+r*(1./3.71)))**2
	return l2

# Nikuradse rugeux (turbulent rugueux):
def Nikuradse_Rug(r):
	l=1./(1.14-2.*math.log10(r))**2
	return l

On peut comparer ce que donne les formule pour le même Reynolds:

In [ ]:
Re=30000
print(Blasius(Re))
print(Nikuradse(Re))
print(IdelCik(Re))
print(K_Nikuradse(Re))

On peut donc calculer la valeur de $\lambda$ en utilisant la bonne formule en fonction du nombre de Reynolds. Maintenant, on va faire une fonction qui choisira la bonne formule pour nous !

In [ ]:
def lcoeff(Re,r=0):
        #En spécifiant r=0 dans les argument de la fonction, 
        #on suppose que si la valeur de r n'est pas donnée par l'utilisateur, elle sera nulle par défaut.
        if Re<2000: #Laminaire
        	 l=64./Re
        elif (Re>=2000 and Re<1e5 and r<=1e-5):
             l=Blasius(Re)
        elif (Re>=2000 and Re<1e5 and r>1e-5):
             l=Collebrook(Re,r)
        elif (Re>=1e5 and r<=1e-5):
             l=Collebrook(Re,r)
        elif (Re>=1e5 and r>1e-5):
             l=Nikuradse_Rug(r)
        return l
    
# Test:
print(lcoeff(500))
print(lcoeff(4000))
print(lcoeff(10000,0.001))
print(lcoeff(1e6,0.001))

La fonction <b>lcoeff</b> renvoie donc la bonne valeur du coefficient $\lambda$ en choisissant la bonne formule a utiliser en fonction du nombre de Reynolds. On peut maintenant utiliser cette fonction pour calculer directement la perte de charge linéaire $\Delta P$ en fonction des grandeurs d'entrée $U,L,D,\nu,r$: 

In [ ]:
def perte_lin(L,D,U,r=1e-6,rho=1000,nu=1e-6):
    #Par defaut on a de l'eau (rho=1000 et nu=1e-6)
	Re=U*D/nu
	dP=lcoeff(Re,r)*(L/D)*0.5*rho*U**2
	return dP

#Exemple: perte de charge dans un tuyau de 1cm de diamètre de 1m de long avec de l'eau à 1m/s de vitesse debitante:
print(perte_lin(1.,0.01,1.)) # Le résultat est en pascal
print(perte_lin(1.,0.01,1.,nu=1e-5))

On peux également construire des fonctions qui utilisent le débit volumique $q_v$ et le débit massique $q_m$ plutôt que la vitesse débitante:    

In [ ]:
def perte_lin_qv(L,D,qv,r=1e-6,rho=1000,nu=1e-6):
    #Par defaut on a de l'eau (rho=1000 et nu=1e-6)
    #Calcul de la section que l'on suppose circulaire:
    S=np.pi*D**2/4.
    U=qv/S
    Re=U*D/nu
    dP=lcoeff(Re,r)*(L/D)*0.5*rho*U**2
    return dP
    
def perte_lin_qm(L,D,qm,r=1e-6,rho=1000,nu=1e-6):
    #Par defaut on a de l'eau (rho=1000 et nu=1e-6)
    #Calcul de la section que l'on suppose circulaire:
    S=np.pi*D**2/4.
    qv=qm/rho
    U=qv/S
    Re=U*D/nu
    dP=lcoeff(Re,r)*(L/D)*0.5*rho*U**2
    return dP

In [ ]:
print("Exemple du doublement de diametre en laminaire :")
print(perte_lin_qv(1.,0.1,0.01,nu=1)/perte_lin_qv(1.,0.2,0.01,nu=1))


print("Exemple du doublement de diametre en turbulent :")
print(perte_lin_qv(1.,0.1,0.01)/perte_lin_qv(1.,0.2,0.01))

In [ ]:
#Exemple du pipeline du TD1:
print(perte_lin_qm(5510.,0.25,18.,rho=900.,nu=0.261/900.))

**Pistes possibles pour aller plus loin:**

* On pourra essayer de retrouver les autres résultats des TD
* Représenter l'évolution du coefficient $\lambda$ en fonction du Reynolds

In [ ]:
Re=np.linspace(200,1e6,20)
for re in Re:
    plt.loglog(re,...)
    ...

In [57]:
from IPython.core.display import HTML
style=open('notebooks.css', "r").read()
HTML(style)

<a id="top" style="float:left;" href="http://dynfluid.ensam.eu/"><img style="height:80px;" src="https://hpp.education/Lessons/docet.png"/></a>
<a style="float:right;" href="http://www.cnam.fr//"><img style="height:80px;" src="https://upload.wikimedia.org/wikipedia/commons/6/66/Logo_cnam.gif"/></a>
<center><a href="#top">Retour en haut de la page</a></center>